In [ ]:
# Copywrite 2024, Duality Robotics

# See how you can use images created from a FalconEditor simulation to train a
# YOLO_v8 model, then test the model on real world images.

# Read the comment instructions and run this colab notebook to see synthetic
# data work on real world images.

# FalconEditor allows users to easily create synthetic datasets tailored to
# their training needs. The FalconEDU subscription provides support (like this!)
# for training and testing.

# This notebook references different informational pages. Create a free Falcon
# account now to access those pages.

# https://falcon.duality.ai/auth/sign-up

# With FalconEDU, you have the instructions and software needed to
# create your own simulation, learn best practices for synthetic data and
# simualation, and collaborate with other learners and experts.


import os, sys
HOME = os.getcwd()
print(HOME)

In [ ]:
# Start with running a GPU enabled instance.  If this
# fails, go to the Edit menu, choose 'Notebook settings' and select a 'T4 GPU'
# under Hardware Accelerator.

# The GPU makes the training go MUCH faster, so it's worth setting up now.

# Not everyone has a GPU enabled computer, and even if you do, Colab still make
# the process easier.

# The FalconEDU subscription contains tips, tricks, and advice for making
# simulation using digital twins, synthetic data, and AI training easier, better,
# and faster!

!nvidia-smi

In [ ]:
# Now we install Ultralytics, the specific python version, and
# CUDA. These are all files needed for training.

# Using Colab prevents you from installing/uninstalling software
# versions, thereby bypassing potential conflicts. Our EDU support
# content helps you navigate these type of hurdles.

!pip install ultralytics==8.2.103 -q

from IPython import display
display.clear_output

import ultralytics
ultralytics.checks()

In [ ]:
# Now we mount (connect) the folder on Drive containing the training data.
# You will have to grant Colab access the drive connected to this Colab Notebook.
# After running the code below, the system will access for credentials - enter
# the ones for the particular Google account that controls the folder that
# contains the Falcon datasets.

# Note:  You may find that this does not work if the notebook and the Drive
# folder are owned by different Google accounts.

from google.colab import drive
drive.mount('/content/drive')

In [ ]:
# Now change directory to the Colab Notebook folder in your drive

# Note: If you didn't have a Colab Notebook folder already, Colab
# created one for you in your drive when you opened this notebook.

%cd /content/drive/MyDrive/Colab Notebooks

In [ ]:
# Clone the training dataset and scripts from the git repo. This may take a
# little bit, but when it's done, you will have a syntheticDataWorks/Output
# folder in your Colab Notebooks folder. Inside will be everything needed for
# training and testing your model.
# Sometimes it takes a couple minutes for Drive to update with all the new files,
# even after this cell is finished running.

# Go into Colab Notebooks/syntheticDataWorks/Output/train/images to see the
# synthetic dataset. Some details of note:


# 1. FalconEditor, our simulation software, has high visual fidelity, allowing
#    it to create effective datasets for Object Detection
# 2. Simulations in FalconEditor allow you to automatically annotate your datasets-
#    saving time, money, and effort and allowing for quick iterations
# 3. This dataset shows a relevant domain (an indoor environment) and a variety of
#    objects. All of these help create effective training, and Duality has a
#    library of assets you can download and use in your simulations to improve
#    performance. Check them out here: https://falcon.duality.ai/secure/digital-twins


! git clone https://github.com/duality-robotics/syntheticDataWorks.git

In [ ]:
# This is a quick test to confirm that you've moved to the right folder and
# that the notebook can access the images.  You can hide the output after the
# test.

from IPython.display import Image
Image('./syntheticDataWorks/Output/train/images/000000001.png')

In [ ]:
#Navigate into the cloned folder

%cd ./syntheticDataWorks/Output

In [ ]:
# Now that we have access to the images, we can run the training script

# Please note that this will take a little while - 20-30 minutes.
# You may need to stay active on the page to avoid a timeout.
# You may notice that the output pauses at times, particuarly at the start.

# While this is running, read our docs explaining the training output:
# https://falcon.duality.ai/secure/documentation/ex-1-training-output

#

%run train.py

In [ ]:
# The above training outputs final metrics in this format:
# Model summary (fused): 168 layers, 11,125,971 parameters, 0 gradients, 28.4 GFLOPs
#                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95): 100%|██████████| 5/5 [00:06<00:00,  1.39s/it]
#                   all        138        136      0.978      0.993      0.993       0.98

#      mAP50
# The  0.993  score is most important, but for this training that uses soley
# synthetic data, this high mAP50 score doesn't necesarily mean it works that well
# on real world images. We'll have to test this model next to see how well it performs
# in the real world.

# You can look at these graphs to check for any errors in the training.
from IPython.display import Image
Image('/content/drive/MyDrive/Colab Notebooks/syntheticDataWorks/Output/runs/detect/train/results.png')

# In depth information is at https://falcon.duality.ai/secure/documentation/colab-ex-1-training-output
# On any graphs that say "loss", you should see a downward trend. If loss starts
# trending up, that means your model is getting worse and you should adjust your
# learning rate

# Precision and Recall should have an upward trend. If the data shoots up and flatlines,
# you are probably overfitting and need more variety in your dataset.

# The mAP50 trend is displayed. It should also have an upward trend, and if it
# starts trending back down, there is a problem

# Creating synthetic data in FalconEditor allows you to adjust your scenario if
# your training has any of these pitfalls, making getting effective training
# data easy, cheap, and accessible.


In [ ]:
# In order to see how the model performs in the physical world, we must test it
# on images from the physcial world.

# Run the test scipt by pressing "play" on this cell.
# This script tells the YOLO model to look at the images in the testImages
# folder and make predictions.

# If this isn't the first time you're run this training,
# the system will prompt you to select which model you'd like to validate. Just
# choose the highest number to test the latest.

# When this is finished, you can find the prediction images
# in ./syntheticDataWorks/Output/predictions')
# You can find the training and testing metrics and graphs in
# ./syntheticDataWorks/Output/runs/detect/. The train folder is from the training
# and the val folder is from the testing.
%run predict.py

In [ ]:
# Again, this process outputs this data:
# val: New cache created: /content/drive/MyDrive/Colab Notebooks/syntheticDataWorks/testImages/labels.cache
#                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95): 100%|██████████| 11/11 [00:13<00:00,  1.22s/it]
#                   all        164        164      0.934       0.87      0.952      0.828

#      mAP50
# The  0.952  score shows that the training worked, and your model can detect Cheerios in a real world setting. Congrats!

# Run this cell to see a grid of the prediction images!

from IPython.display import Image
Image('/content/drive/MyDrive/Colab Notebooks/syntheticDataWorks/Output/runs/detect/val/val_batch0_pred.jpg')


# You can see the full size, annotated predictions of the real world images here:
# ./syntheticDataWorks/Output/predictions

# You can also see various output data in ./syntheticDataWorks/Output/runs/detect/val
# You can read explanations of the output data (including a breakdown of
# the an mAP50 score meaning) here:
# https://falcon.duality.ai/secure/documentation/colab-ex-1-testing-output


In [ ]:
# You have successfully trained a YOLO8 model using synthetic data from FalconEditor!

# You got a high mAP50 score (above .9), but some use cases need better! One manufacturing
# client needed a mAP50 >= .99. How would you improve your training?

# First, you'd look at the false negatives and positive to see if there's an identifiable
# and fixable trend.

# This prediction set had very few false positives (identifing something as a cheerio
# box that isn't one), so let's look at the false negatives.

# Run this code to create a 3x4 grid of false negative predictions.

from enum import auto
from IPython.display import display
from ipywidgets import widgets, HBox, Layout
from ipywidgets import interact, interactive, fixed, interact_manual

l = Layout(flex='0 1 auto', height='30px', min_height='40px', width='10')
imageA = widgets.Image(value=open('/content/drive/MyDrive/Colab Notebooks/syntheticDataWorks/Output/predictions/images/0367.jpg', 'rb').read(), layout = Layout(flex='0 1 auto', height='300px', min_height='40px', width='auto'))
imageB = widgets.Image(value=open('/content/drive/MyDrive/Colab Notebooks/syntheticDataWorks/Output/predictions/images/0313.jpg', 'rb').read(), layout = Layout(flex='0 1 auto', height='300px', min_height='40px', width='auto'))
imageC = widgets.Image(value=open('/content/drive/MyDrive/Colab Notebooks/syntheticDataWorks/Output/predictions/images/0276 (2).jpg', 'rb').read(), layout = Layout(flex='0 1 auto', height='300px', min_height='40px', width='auto'))
imageD = widgets.Image(value=open('/content/drive/MyDrive/Colab Notebooks/syntheticDataWorks/Output/predictions/images/0266.jpg', 'rb').read(), layout = Layout(flex='0 1 auto', height='300px', min_height='40px', width='auto'))

imageE = widgets.Image(value=open('/content/drive/MyDrive/Colab Notebooks/syntheticDataWorks/Output/predictions/images/0255.jpg', 'rb').read(), layout = Layout(flex='0 1 auto', height='300px', min_height='40px', width='auto'))
imageF = widgets.Image(value=open('/content/drive/MyDrive/Colab Notebooks/syntheticDataWorks/Output/predictions/images/0244.jpg', 'rb').read(), layout = Layout(flex='0 1 auto', height='300px', min_height='40px', width='auto'))
imageG = widgets.Image(value=open('/content/drive/MyDrive/Colab Notebooks/syntheticDataWorks/Output/predictions/images/0229.jpg', 'rb').read(), layout = Layout(flex='0 1 auto', height='300px', min_height='40px', width='auto'))
imageH = widgets.Image(value=open('/content/drive/MyDrive/Colab Notebooks/syntheticDataWorks/Output/predictions/images/0172.jpg', 'rb').read(), layout = Layout(flex='0 1 auto', height='300px', min_height='40px', width='auto'))

imageI = widgets.Image(value=open('/content/drive/MyDrive/Colab Notebooks/syntheticDataWorks/Output/predictions/images/0172 (2).jpg', 'rb').read(), layout = Layout(flex='0 1 auto', height='300px', min_height='40px', width='auto'))
imageJ = widgets.Image(value=open('/content/drive/MyDrive/Colab Notebooks/syntheticDataWorks/Output/predictions/images/0140.jpg', 'rb').read(), layout = Layout(flex='0 1 auto', height='300px', min_height='40px', width='auto'))
imageK = widgets.Image(value=open('/content/drive/MyDrive/Colab Notebooks/syntheticDataWorks/Output/predictions/images/0054.jpg', 'rb').read(), layout = Layout(flex='0 1 auto', height='300px', min_height='40px', width='auto'))
imageL = widgets.Image(value=open('/content/drive/MyDrive/Colab Notebooks/syntheticDataWorks/Output/predictions/images/0012 (2).jpg', 'rb').read(), layout = Layout(flex='0 1 auto', height='300px', min_height='40px', width='auto'))

hbox0 = HBox([imageA, imageB, imageC, imageD])
hbox1 = HBox([imageE, imageF, imageG, imageH])
hbox2 = HBox([imageI, imageJ, imageK, imageL])

display(hbox0)
display(hbox1)
display(hbox2)


In [ ]:
# One clear trend is that almost all of these images have some occlusion, or
# objects in front of them, obscuring them in some way.

# A clear way to push the mAP50 score higher is to work on producing more
# occluded training images. See this doc page for suggestions on how to do that:
# https://falcon.duality.ai/secure/documentation/colab-ex-1-whats-next

# The EDU subscription provides you with access to FalconEditor and the scenario
# we used to create this synthetic dataset.
# Sign up for the EDU free trial to create a new dataset, easily adjusting parameters
# until you find success. Explore the high power capabilites of FalconEditor to
# quickly iterate through different datasets until you find what works.

# Along the way, learn skills for quickly and effectively identifying the factors
# that make a successful synthetic dataset.



# Join our EDU subscription and learn to create and optimize synthetic datasets
# for AI vision model training! https://www.duality.ai/edu

# Follow us on Linkedin to keep uptodate on new exercise, classes, and webinars!
# https://www.linkedin.com/company/dualityai